<a href="https://colab.research.google.com/github/baussel/Satellite_Detection/blob/main/Hubble_Image_Download.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Hubble Image Download



---


*Ben Aussel, August 2021, ESA*


---



In [ ]:
#Mount Google Drive with this Colab
from google.colab import drive
drive.mount('/content/drive',force_remount=True)

Mounted at /content/drive


## Modules

In [ ]:
#Modules
from PIL import Image
import PIL
import os
import numpy as np
from urllib.request import urlretrieve
from urllib.error import HTTPError
import urllib
import pandas as pd
import time
import glob
import requests
from tqdm import tqdm

## Main functions

In [ ]:
url_base_comp = "https://hst-int.esac.esa.int/preview/"
url_base_single = "http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID="
url_base = "https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID="

path_images = "/content/drive/MyDrive/ESA/Data/Hubble_Images/"

def download_image(o_id,id,camera,obs_type):
    try:
        if camera=="ACS/WFC":
            if obs_type=="HST Singleton":
                url = url_base_single+id+"_raw.jpg"
                urlretrieve(url,path_images+"Raw/ACS_Singleton/"+o_id+"_"+id+".jpg")
            else:
                url = url_base_comp+"ACS/"+id+"_flc.fits.jpg"
                urlretrieve(url,path_images+"Raw/ACS_Comp_Raw/"+o_id+"_"+id+".jpg")
            print("Image URL:",url)
        elif camera =="WFC3/UVIS":
            if obs_type=="HST Singleton":
                url = url_base_single+id+"_raw.jpg"
                urlretrieve(url,path_images+"Raw/WFC3_UVIS_Singleton/"+o_id+"_"+id+".jpg")
            else:
                url = url_base_comp+"WFC3/"+id+"_flc.fits.jpg"
                urlretrieve(url,path_images+"Raw/WFC3_UVIS_Comp_Raw/"+o_id+"_"+id+".jpg")
            print("Image URL:",url)
        elif camera == "WFC3/IR":
            if obs_type=="HST Singleton":
                url = url_base_single+id+"_raw.jpg"
                urlretrieve(url,path_images+"Raw/WFC3_IR_Singleton/"+o_id+"_"+id+".jpg")
            else:
                url = url_base+id
                urlretrieve(url,path_images+"Raw/WFC3_IR_Comp_Raw/"+o_id+"_"+id+".jpg")
            print("Image URL:",url)
        else:
            print("WRONG CAMERA...")
        return ""
    except(urllib.error.HTTPError):
        print("Link not working Error!")
        return "Error"
    except:
        print("Connection abort Error!")
        return ""

In [ ]:
def get_raw_ids(number,members):
    try:
        ids = []
        splitted = members.split()
        for i in range(len(splitted)):
            ids.append(splitted[i].replace("caom:HST/",""))
        print("IDs:",ids)
        return ids
    except:
        print("Member error.")

## Download

### Composite

#### ACS/WFC

In [ ]:
#ACS Composite - 4 parts
data_ACS_R = pd.read_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/csv_for_download/ACS_Composite.csv")
print("---ACS_Composite:---")
print("Dataset contains",len(data_ACS_R),"composite images")
print("It contains",data_ACS_R.sum(axis=0)["members_number"],"raw images")
print("----")
MAX_SIZE = (600,600)
print("Downloading all images and compressing them to",MAX_SIZE)
failure_ids = []

---ACS_Composite:---
Dataset contains 28322 composite images
It contains 89341 raw images
----


In [ ]:
def download_part_ACS_comp(start,end):
    starttime = time.time()
    for i in range(start,end):
        print("---",i,"/",end,"---")
        raw_ids = get_raw_ids(data_ACS_R["members_number"][i],data_ACS_R["members"][i])
        for j in range(0,len(raw_ids)):
            error = download_image(data_ACS_R["observation_id"][i],raw_ids[j],"ACS/WFC","HST Composite")
            if error == "Error":
                failure_ids.append(data_ACS_R["observation_id"][i]+"_"+raw_ids[j])
            else:
                try:
                    path = path_images+"Raw/ACS_Comp_Raw/"+data_ACS_R["observation_id"][i]+"_"+raw_ids[j]+".jpg"
                    im = PIL.Image.open(path)
                    #RESIZE
                    im1 = im.resize(MAX_SIZE)
                    #save resized images in folder
                    im1.save(path)
                    print("-> Compressed and saved:", path)
                except:
                    print("Compression Error!")
    print("That took {} seconds".format(time.time() - starttime))
    print("Number of failed downloads:",len(failure_ids))

In [ ]:
print("//////DOWNLOADING PART 1\\\\\\")
print("Indices",0,"to",int(len(data_ACS_R)/4)-1)
download_part_ACS_comp(0,int(len(data_ACS_R)/4))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_ACS_comp_Raw_1.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
Image URL: https://hst-int.esac.esa.int/preview/ACS/jdxf19gqq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jdxf19010_jdxf19gqq.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jdxf19gsq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jdxf19010_jdxf19gsq.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jdxf19gvq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jdxf19010_jdxf19gvq.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jdxf19gzq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jdxf19010_jdxf19gzq.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jdxf19h2q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jdxf19010_jdxf19h2q.jp

UnboundLocalError: ignored

In [ ]:
print("//////DOWNLOADING PART 2\\\\\\")
print("Indices",int(len(data_ACS_R)/4),"to",int(len(data_ACS_R)/2)-1)
failure_ids = []
download_part_ACS_comp(int(len(data_ACS_R)/4),int(len(data_ACS_R)/2))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_ACS_comp_Raw_2.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jcdm0b020_jcdm0bnjq.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jcdm0bnyq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jcdm0b020_jcdm0bnyq.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jcdm0bonq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jcdm0b020_jcdm0bonq.jpg
--- 13519 / 14161 ---
IDs: ['jcqt94aeq', 'jcqt94yzq', 'jcqt94z6q', 'jcqt94ziq']
Image URL: https://hst-int.esac.esa.int/preview/ACS/jcqt94aeq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jcqt94020_jcqt94aeq.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jcqt94yzq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jcqt94020_jcqt94y

In [ ]:
print("//////DOWNLOADING PART 3\\\\\\")
print("Indices",int(len(data_ACS_R)/2),"to",int(len(data_ACS_R)*3/4)-1)
failure_ids = []
download_part_ACS_comp(int(len(data_ACS_R)/2),int(len(data_ACS_R)*3/4))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_ACS_comp_Raw_3.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jbyr06010_jbyr06xzq.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jbyr06y2q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jbyr06010_jbyr06y2q.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jbyr06y6q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jbyr06010_jbyr06y6q.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jbyr06y9q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jbyr06010_jbyr06y9q.jpg
--- 20621 / 21241 ---
IDs: ['j8xi30c9q', 'j8xi30caq', 'j8xi30ccq', 'j8xi30ceq']
Image URL: https://hst-int.esac.esa.int/preview/ACS/j8xi30c9q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/j8xi30010_j8xi30c

In [ ]:
print("//////DOWNLOADING PART 4\\\\\\")
print("Indices",int(len(data_ACS_R)*3/4),"to",int(len(data_ACS_R))-1)
failure_ids = []
download_part_ACS_comp(int(len(data_ACS_R)*3/4),int(len(data_ACS_R)))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_ACS_comp_Raw_4.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/ja2s1a010_ja2s1akbq.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/ja2s1akfq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/ja2s1a010_ja2s1akfq.jpg
--- 27561 / 28322 ---
IDs: ['jdjy01o0q', 'jdjy01o2q']
Image URL: https://hst-int.esac.esa.int/preview/ACS/jdjy01o0q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jdjy01010_jdjy01o0q.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jdjy01o2q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw/jdjy01010_jdjy01o2q.jpg
--- 27562 / 28322 ---
IDs: ['jc6i05e2q', 'jc6i05e5q', 'jc6i05e9q', 'jc6i05ecq', 'jc6i05ehq', 'jc6i05ekq', 'jc6i05eoq', 'jc6i05erq']
Image URL: https://hst-int.esac.esa.int/preview/ACS/jc6i05e2q_flc.fits.jpg

Images for 2021 (file created 15/11/2021)

In [ ]:
url_base_comp = "https://hst-int.esac.esa.int/preview/"
url_base_single = "http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID="
url_base = "https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID="

path_images = "/content/drive/MyDrive/ESA/Data/Hubble_Images/"

def download_image(o_id,id,camera,obs_type):
    try:
        if camera=="ACS/WFC":
            if obs_type=="HST Singleton":
                url = url_base_single+id+"_raw.jpg"
                urlretrieve(url,path_images+"Raw/ACS_Singleton/"+o_id+"_"+id+".jpg")
            else:
                url = url_base_comp+"ACS/"+id+"_flc.fits.jpg"
                urlretrieve(url,path_images+"Raw/ACS_Comp_Raw_2021/"+o_id+"_"+id+".jpg")
            print("Image URL:",url)
        elif camera =="WFC3/UVIS":
            if obs_type=="HST Singleton":
                url = url_base_single+id+"_raw.jpg"
                urlretrieve(url,path_images+"Raw/WFC3_UVIS_Singleton/"+o_id+"_"+id+".jpg")
            else:
                url = url_base_comp+"WFC3/"+id+"_flc.fits.jpg"
                urlretrieve(url,path_images+"Raw/WFC3_UVIS_Comp_Raw_2021/"+o_id+"_"+id+".jpg")
            print("Image URL:",url)
        elif camera == "WFC3/IR":
            if obs_type=="HST Singleton":
                url = url_base_single+id+"_raw.jpg"
                urlretrieve(url,path_images+"Raw/WFC3_IR_Singleton/"+o_id+"_"+id+".jpg")
            else:
                url = url_base+id
                urlretrieve(url,path_images+"Raw/WFC3_IR_Comp_Raw_2021/"+o_id+"_"+id+".jpg")
            print("Image URL:",url)
        else:
            print("WRONG CAMERA...")
        return ""
    except(urllib.error.HTTPError):
        print("Link not working Error!")
        return "Error"
    except:
        print("Connection abort Error!")
        return ""

In [ ]:
def download_part_ACS_comp(start,end):
    starttime = time.time()
    for i in range(start,end):
        print("---",i,"/",end,"---")
        raw_ids = get_raw_ids(data_ACS_R["members_number"][i],data_ACS_R["members"][i])
        for j in range(0,len(raw_ids)):
            error = download_image(data_ACS_R["observation_id"][i],raw_ids[j],"ACS/WFC","HST Composite")
            if error == "Error":
                failure_ids.append(data_ACS_R["observation_id"][i]+"_"+raw_ids[j])
            else:
                try:
                    path = path_images+"Raw/ACS_Comp_Raw_2021/"+data_ACS_R["observation_id"][i]+"_"+raw_ids[j]+".jpg"
                    im = PIL.Image.open(path)
                    #RESIZE
                    im1 = im.resize(MAX_SIZE)
                    #save resized images in folder
                    im1.save(path)
                    print("-> Compressed and saved:", path)
                except:
                    print("Compression Error!")
    print("That took {} seconds".format(time.time() - starttime))
    print("Number of failed downloads:",len(failure_ids))

In [ ]:
#ACS Composite 2021
data_ACS_R = pd.read_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/csv_for_download/2021/ACS_Composite_2021.csv")
print("---ACS_Composite:---")
print("Dataset contains",len(data_ACS_R),"composite images")
print("It contains",data_ACS_R.sum(axis=0)["members_number"],"raw images")
print("----")
MAX_SIZE = (600,600)
print("Downloading all images and compressing them to",MAX_SIZE)
failure_ids = []

---ACS_Composite:---
Dataset contains 842 composite images
It contains 2384 raw images
----


In [ ]:
print("//////DOWNLOADING Images for 2021\\\\\\")
download_part_ACS_comp(0,len(data_ACS_R))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_ACS_comp_Raw_2021.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
--- 155 / 842 ---
IDs: ['je3w01xwq', 'je3w01y0q']
Image URL: https://hst-int.esac.esa.int/preview/ACS/je3w01xwq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw_2021/je3w01020_je3w01xwq.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/je3w01y0q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw_2021/je3w01020_je3w01y0q.jpg
--- 156 / 842 ---
IDs: ['jecd61g9q', 'jecd61gbq', 'jecd61geq', 'jecd61giq']
Image URL: https://hst-int.esac.esa.int/preview/ACS/jecd61g9q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw_2021/jecd61010_jecd61g9q.jpg
Image URL: https://hst-int.esac.esa.int/preview/ACS/jecd61gbq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/ACS_Comp_Raw_2021/jecd61010_jecd61gbq.jpg
Image URL: https://hst-int.esac.esa.int

#### WFC3/UVIS

In [ ]:
#WFC3/UVIS Composite - 4 parts
data_WFC3_UVIS_R = pd.read_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/csv_for_download/WFC3_UVIS_Composite.csv")
print("---WFC3_UVIS_Composite:---")
print("Dataset contains",len(data_WFC3_UVIS_R),"composite images")
print("It contains",data_WFC3_UVIS_R.sum(axis=0)["members_number"],"raw images")
print("----")
MAX_SIZE = (600,600)
print("Downloading all images and compressing them to",MAX_SIZE)
failure_ids = []
compression_error = 0 

---WFC3_UVIS_Composite:---
Dataset contains 23365 composite images
It contains 71857 raw images
----


In [ ]:
def download_part_WFC3_UVIS_comp(start,end):
    starttime = time.time()
    for i in range(start,end):
        print("---",i,"/",end,"---")
        raw_ids = get_raw_ids(data_WFC3_UVIS_R["members_number"][i],data_WFC3_UVIS_R["members"][i])
        for j in range(0,len(raw_ids)):
            error = download_image(data_WFC3_UVIS_R["observation_id"][i],raw_ids[j],"WFC3/UVIS","HST Composite")
            if error == "Error":
                failure_ids.append(data_WFC3_UVIS_R["observation_id"][i]+"_"+raw_ids[j])
            else:
                try:
                    path = path_images+"Raw/WFC3_UVIS_Comp_Raw/"+data_WFC3_UVIS_R["observation_id"][i]+"_"+raw_ids[j]+".jpg"
                    im = PIL.Image.open(path)
                    #RESIZE
                    im1 = im.resize(MAX_SIZE)
                    #save resized images in folder
                    im1.save(path)
                    print("-> Compressed and saved:", path)
                except:
                    print("Compression Error!")
    print("That took {} seconds".format(time.time() - starttime))
    print("Number of failed downloads:",len(failure_ids))

In [ ]:
print("//////DOWNLOADING PART 1\\\\\\")
print("Indices",0,"to",int(len(data_WFC3_UVIS_R)/4)-1)
download_part_WFC3_UVIS_comp(0,int(len(data_WFC3_UVIS_R)/4))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_WFC3_UVIS_comp_Raw_1.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/ibsr07020_ibsr07ndq.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/ibsr07njq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/ibsr07020_ibsr07njq.jpg
--- 5165 / 5840 ---
IDs: ['idb610ziq', 'idb610zoq']
Image URL: https://hst-int.esac.esa.int/preview/WFC3/idb610ziq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/idb610030_idb610ziq.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/idb610zoq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/idb610030_idb610zoq.jpg
--- 5166 / 5840 ---
IDs: ['ibbsz9k8q', 'ibbsz9k9q']
Image URL: https://hst-int.esac.esa.int/preview/WFC3/ibbsz9k8q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/D

In [ ]:
print("//////DOWNLOADING PART 2\\\\\\")
print("Indices",int(len(data_WFC3_UVIS_R)/4),"to",int(len(data_WFC3_UVIS_R)/2)-1)
failure_ids = []
download_part_WFC3_UVIS_comp(int(len(data_WFC3_UVIS_R)/4),int(len(data_WFC3_UVIS_R)/2))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_WFC3_UVIS_comp_Raw_2.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
Image URL: https://hst-int.esac.esa.int/preview/WFC3/ibqf01edq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/ibqf010d0_ibqf01edq.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/ibqf01ejq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/ibqf010d0_ibqf01ejq.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/ibqf01exq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/ibqf010d0_ibqf01exq.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/ibqf01f2q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/ibqf010d0_ibqf01f2q.jpg
--- 11049 / 5840 ---
IDs: ['ib5712uoq', 'ib5712upq', 'ib5712uqq', 'ib5712urq']
Link not working Error!
Link not working Error!
Link not working Error!
Link n

In [ ]:
print("//////DOWNLOADING PART 3\\\\\\")
print("Indices",int(len(data_WFC3_UVIS_R)/2),"to",int(len(data_WFC3_UVIS_R)*3/4)-1)
failure_ids = []
download_part_WFC3_UVIS_comp(int(len(data_WFC3_UVIS_R)/2),int(len(data_WFC3_UVIS_R)*3/4))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_WFC3_UVIS_comp_Raw_3.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
Image URL: https://hst-int.esac.esa.int/preview/WFC3/icas01oaq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/icas01010_icas01oaq.jpg
--- 16878 / 5840 ---
IDs: ['idg801epq', 'idg801esq', 'idg801ewq', 'idg801f0q']
Image URL: https://hst-int.esac.esa.int/preview/WFC3/idg801epq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/idg801010_idg801epq.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/idg801esq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/idg801010_idg801esq.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/idg801ewq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/idg801010_idg801ewq.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/idg801f0q_flc.fits.jpg
->

In [ ]:
print("//////DOWNLOADING PART 4\\\\\\")
print("Indices",int(len(data_WFC3_UVIS_R)*3/4),"to",int(len(data_WFC3_UVIS_R))-1)
failure_ids = []
download_part_WFC3_UVIS_comp(int(len(data_WFC3_UVIS_R)*3/4),int(len(data_WFC3_UVIS_R)))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_WFC3_UVIS_comp_Raw_4.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
--- 22700 / 5840 ---
IDs: ['ib5701lkq', 'ib5701llq', 'ib5701lmq', 'ib5701lnq']
Link not working Error!
Link not working Error!
Link not working Error!
Link not working Error!
--- 22701 / 5840 ---
IDs: ['idxr09yuq', 'idxr09z7q', 'idxr09zkq']
Image URL: https://hst-int.esac.esa.int/preview/WFC3/idxr09yuq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/idxr09050_idxr09yuq.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/idxr09z7q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/idxr09050_idxr09z7q.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/idxr09zkq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_UVIS_Comp_Raw/idxr09050_idxr09zkq.jpg
--- 22702 / 5840 ---
IDs: ['iabk04j7q', 'iabk04j8q']
Link not working Error!
Link not working Error!
--- 22703

##### Images of 2021 (15/11/21)

In [ ]:
url_base_comp = "https://hst-int.esac.esa.int/preview/"
url_base_single = "http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID="
url_base = "https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID="

path_images = "/content/drive/MyDrive/ESA/Data/Hubble_Images/"

def download_image(o_id,id,camera,obs_type):
    try:
        if camera=="ACS/WFC":
            if obs_type=="HST Singleton":
                url = url_base_single+id+"_raw.jpg"
                urlretrieve(url,path_images+"Raw/ACS_Singleton/"+o_id+"_"+id+".jpg")
            else:
                url = url_base_comp+"ACS/"+id+"_flc.fits.jpg"
                urlretrieve(url,path_images+"Raw/ACS_Comp_Raw_2021/"+o_id+"_"+id+".jpg")
            print("Image URL:",url)
        elif camera =="WFC3/UVIS":
            if obs_type=="HST Singleton":
                url = url_base_single+id+"_raw.jpg"
                urlretrieve(url,path_images+"Raw/WFC3_UVIS_Singleton/"+o_id+"_"+id+".jpg")
            else:
                url = url_base_comp+"WFC3/"+id+"_flc.fits.jpg"
                urlretrieve(url,path_images+"Raw/WFC3_Comp_Raw_2021/"+o_id+"_"+id+".jpg")
            print("Image URL:",url)
        elif camera == "WFC3/IR":
            if obs_type=="HST Singleton":
                url = url_base_single+id+"_raw.jpg"
                urlretrieve(url,path_images+"Raw/WFC3_IR_Singleton/"+o_id+"_"+id+".jpg")
            else:
                url = url_base+id
                urlretrieve(url,path_images+"Raw/WFC3_IR_Comp_Raw_2021/"+o_id+"_"+id+".jpg")
            print("Image URL:",url)
        else:
            print("WRONG CAMERA...")
        return ""
    except(urllib.error.HTTPError):
        print("Link not working Error!")
        return "Error"
    except:
        print("Connection abort Error!")
        return ""

In [ ]:
def download_part_WFC3_comp(start,end):
    starttime = time.time()
    for i in range(start,end):
        print("---",i,"/",end,"---")
        raw_ids = get_raw_ids(data_WFC3_R["members_number"][i],data_WFC3_R["members"][i])
        for j in range(0,len(raw_ids)):
            error = download_image(data_WFC3_R["observation_id"][i],raw_ids[j],"WFC3/UVIS","HST Composite")
            if error == "Error":
                failure_ids.append(data_WFC3_R["observation_id"][i]+"_"+raw_ids[j])
            else:
                try:
                    path = path_images+"Raw/WFC3_Comp_Raw_2021/"+data_WFC3_R["observation_id"][i]+"_"+raw_ids[j]+".jpg"
                    im = PIL.Image.open(path)
                    #RESIZE
                    im1 = im.resize(MAX_SIZE)
                    #save resized images in folder
                    im1.save(path)
                    print("-> Compressed and saved:", path)
                except:
                    print("Compression Error!")
    print("That took {} seconds".format(time.time() - starttime))
    print("Number of failed downloads:",len(failure_ids))

In [ ]:
#WFC3 Composite 2021
data_WFC3_R = pd.read_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/csv_for_download/2021/WFC3_UVIS_Composite_2021.csv")
print("---ACS_Composite:---")
print("Dataset contains",len(data_WFC3_R),"composite images")
print("It contains",data_WFC3_R.sum(axis=0)["members_number"],"raw images")
print("----")
MAX_SIZE = (600,600)
print("Downloading all images and compressing them to",MAX_SIZE)
failure_ids = []

---ACS_Composite:---
Dataset contains 1436 composite images
It contains 4300 raw images
----


In [ ]:
print("//////DOWNLOADING Images for 2021\\\\\\")
download_part_WFC3_comp(0,len(data_WFC3_R))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_WFC3_comp_Raw_2021.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_Comp_Raw_2021/iedv02010_iedv02kbq.jpg
--- 793 / 1436 ---
IDs: ['ie4i22m5q', 'ie4i22m8q', 'ie4i22mcq', 'ie4i22mgq']
Image URL: https://hst-int.esac.esa.int/preview/WFC3/ie4i22m5q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_Comp_Raw_2021/ie4i22010_ie4i22m5q.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/ie4i22m8q_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_Comp_Raw_2021/ie4i22010_ie4i22m8q.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/ie4i22mcq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_Comp_Raw_2021/ie4i22010_ie4i22mcq.jpg
Image URL: https://hst-int.esac.esa.int/preview/WFC3/ie4i22mgq_flc.fits.jpg
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_

#### WFC3/IR

In [ ]:
#WFC3/IR Composite - 4 parts
data_WFC3_IR_R = pd.read_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/csv_for_download/WFC3_IR_Composite.csv")
print("---WFC3_IR_Composite:---")
print("Dataset contains",len(data_WFC3_IR_R),"composite images")
print("It contains",data_WFC3_IR_R.sum(axis=0)["members_number"],"raw images")
print("----")
MAX_SIZE = (600,600)
print("Downloading all images and compressing them to",MAX_SIZE)
failure_ids = []
compression_error = 0 

---WFC3_IR_Composite:---
Dataset contains 22045 composite images
It contains 85611 raw images
----


In [ ]:
def download_part_WFC3_IR_comp(start,end):
    starttime = time.time()
    for i in range(start,end):
        print("---",i,"/",end,"---")
        raw_ids = get_raw_ids(data_WFC3_IR_R["members_number"][i],data_WFC3_IR_R["members"][i])
        for j in range(0,len(raw_ids)):
            error = download_image(data_WFC3_IR_R["observation_id"][i],raw_ids[j],"WFC3/IR","HST Composite")
            if error == "Error":
                failure_ids.append(data_WFC3_IR_R["observation_id"][i]+"_"+raw_ids[j])
            else:
                try:
                    path = path_images+"Raw/WFC3_IR_Comp_Raw/"+data_WFC3_IR_R["observation_id"][i]+"_"+raw_ids[j]+".jpg"
                    im = PIL.Image.open(path)
                    #RESIZE
                    im1 = im.resize(MAX_SIZE)
                    #save resized images in folder
                    im1.save(path)
                    print("-> Compressed and saved:", path)
                except:
                    print("Compression Error!")
    print("That took {} seconds".format(time.time() - starttime))
    print("Number of failed downloads:",len(failure_ids))

In [ ]:
print("//////DOWNLOADING PART 1\\\\\\")
print("Indices",0,"to",int(len(data_WFC3_IR_R)/4)-1)
download_part_WFC3_IR_comp(0,int(len(data_WFC3_IR_R)/4))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_WFC3_IR_comp_Raw_1.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=iccq09dzq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/iccq09060_iccq09dzq.jpg
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=iccq09e3q
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/iccq09060_iccq09e3q.jpg
--- 4996 / 5511 ---
IDs: ['idncc4vvq', 'idncc4w2q', 'idncc4w4q']
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=idncc4vvq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/idncc4030_idncc4vvq.jpg
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=idncc4w2q
-> Compressed and saved: /content/drive/

In [ ]:
print("//////DOWNLOADING PART 2\\\\\\")
print("Indices",int(len(data_WFC3_IR_R)/4),"to",int(len(data_WFC3_IR_R)/2)-1)
failure_ids = []
download_part_WFC3_IR_comp(int(len(data_WFC3_IR_R)/4),int(len(data_WFC3_IR_R)/2))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_WFC3_IR_comp_Raw_2.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=ic2i26oxq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/ic2i26020_ic2i26oxq.jpg
--- 10492 / 11022 ---
IDs: ['ic0dd1cjq', 'ic0dd1cmq', 'ic0dd1coq', 'ic0dd1cqq']
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=ic0dd1cjq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/ic0dd1010_ic0dd1cjq.jpg
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=ic0dd1cmq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/ic0dd1010_ic0dd1cmq.jpg
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=ic0dd1coq
-> Compressed and saved: 

In [ ]:
print("//////DOWNLOADING PART 3\\\\\\")
print("Indices",int(len(data_WFC3_IR_R)/2),"to",int(len(data_WFC3_IR_R)*3/4)-1)
failure_ids = []
download_part_WFC3_IR_comp(int(len(data_WFC3_IR_R)/2),int(len(data_WFC3_IR_R)*3/4))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_WFC3_IR_comp_Raw_3.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
--- 15997 / 16533 ---
IDs: ['icytr1cxq', 'icytr1cyq', 'icytr1czq', 'icytr1d0q']
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=icytr1cxq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/icytr1050_icytr1cxq.jpg
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=icytr1cyq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/icytr1050_icytr1cyq.jpg
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=icytr1czq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/icytr1050_icytr1czq.jpg
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=icytr1d0q
-> Compressed and saved: 

In [ ]:
print("//////DOWNLOADING PART 4\\\\\\")
print("Indices",int(len(data_WFC3_IR_R)*3/4),"to",int(len(data_WFC3_IR_R))-1)
failure_ids = []
download_part_WFC3_IR_comp(int(len(data_WFC3_IR_R)*3/4),int(len(data_WFC3_IR_R)))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_WFC3_IR_comp_Raw_4.csv")

Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
--- 21565 / 22045 ---
IDs: ['ie0x03bnq', 'ie0x03boq', 'ie0x03bsq', 'ie0x03bxq']
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=ie0x03bnq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/ie0x03010_ie0x03bnq.jpg
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=ie0x03boq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/ie0x03010_ie0x03boq.jpg
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=ie0x03bsq
-> Compressed and saved: /content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/WFC3_IR_Comp_Raw/ie0x03010_ie0x03bsq.jpg
Image URL: https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID=ie0x03bxq
-> Compressed and saved: 

## Full Resolution

### ACS

In [ ]:
url_base_comp = "https://hst-int.esac.esa.int/preview/"
url_base_single = "http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID="
url_base = "https://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=POSTCARD&OBSERVATION_ID="

path_images = "/content/drive/MyDrive/ESA/Results/processed/new/full_res/"

In [ ]:
#ACS
data_ACS = pd.read_csv("/content/drive/MyDrive/ESA/Results/processed/new/satellites_ACS_new_processed_params_merged.csv")
print("---ACS:---")
print("Dataset contains",len(data_ACS),"images with satellites.")
print("----------")
print(data_ACS["observation_id"])

---ACS:---
Dataset contains 2423 images with satellites.
----------
0       j6fl1elvq
1       j6fl23pyq
2       j6fl6cilq
3       j6fl6xfuq
4       j6fl7bpoq
          ...    
2418    jeiu04i4q
2419    jeiu04i5q
2420    jeiu04ihq
2421    jeiu09lzq
2422    jeiu11mpq
Name: observation_id, Length: 2423, dtype: object


In [ ]:
for i in tqdm(range(len(data_ACS))):
    filename = data_ACS["composite_id"][i].replace("/content/drive/MyDrive/ESA/Results/processed/new/ACS/","")+"_"+data_ACS["observation_id"][i]+".jpg"
    raw_id = data_ACS["observation_id"][i]
    url = url_base_comp+"ACS/"+raw_id+"_flc.fits.jpg"
    try:
        urlretrieve(url,path_images+filename)
    except:
        print("Download failed:",raw_id)

 44%|████▍     | 1064/2423 [29:54<26:41,  1.18s/it]

Download failed: jbew0qqgq


100%|██████████| 2423/2423 [1:07:02<00:00,  1.66s/it]


In [ ]:
#WFC3
data_WFC3 = pd.read_csv("/content/drive/MyDrive/ESA/Results/processed/new/satellites_WFC3_new_processed_params_merged.csv")
print("---WFC3:---")
print("Dataset contains",len(data_WFC3),"images with satellites.")
print("----------")
print(data_WFC3["observation_id"])

---WFC3:---
Dataset contains 685 images with satellites.
----------
0      ib1f31e9q
1      ib1f32uzq
2      ib1f35igq
3      ib2d02g6q
4      ib2g01gnq
         ...    
680    iehz02c1q
681    iehz03foq
682    iehz03ftq
683    iejc03mmq
684    iejn01grq
Name: observation_id, Length: 685, dtype: object


In [ ]:
for i in tqdm(range(len(data_WFC3))):
    filename = data_WFC3["composite_id"][i].replace("/content/drive/MyDrive/ESA/Results/processed/new/WFC3/","")+"_"+data_WFC3["observation_id"][i]+".jpg"
    raw_id = data_WFC3["observation_id"][i]
    url = url_base_comp+"WFC3/"+raw_id+"_flc.fits.jpg"
    try:
        urlretrieve(url,path_images+filename)
    except:
        print("Download failed:",raw_id)

100%|██████████| 685/685 [17:33<00:00,  1.54s/it]


In [ ]:
#WFC3/IR
data_IR = pd.read_csv("/content/drive/MyDrive/ESA/Results/processed/satellites_IR_processed.csv")
print("---IR:---")
print("Dataset contains",len(data_IR),"images with satellites.")
print("----------")
print(data_IR["filename"])

FileNotFoundError: ignored

In [ ]:
for i in tqdm(range(len(data_IR))):
    filename = data_IR["filename"][i]
    raw_id = filename.split(".")[0].split("_")[1]
    url = url_base+raw_id
    urlretrieve(url,path_images+"satellites_IR/"+filename)

100%|██████████| 651/651 [17:42<00:00,  1.63s/it]


### Singleton

In [ ]:
#ACS Singleton
data_ACS_S = pd.read_csv("ACS_Singleton.csv")
print("---ACS_Singleton:---")
print("Dataset contains",len(data_ACS_S),"images")
print("----")
MAX_SIZE = (600,600)
print("Downloading all images and compressing them to",MAX_SIZE)
failure_ids = []

In [ ]:
def download_part_ACS_sing(start,end):
    starttime = time.time()
    for i in range(start,end):
        print("---",i,"/",end,"---")
        error = download_image(data_ACS_S["observation_id"][i],data_ACS_S["observation_id"][i],"ACS/WFC","HST Singleton")
        if error == "Error":
            failure_ids.append(data_ACS_S["observation_id"][i])
        else:
            try:
                path = path_images+"Raw/ACS_Singleton/"+data_ACS_S["observation_id"][i]+".jpg"
                im = PIL.Image.open(path)
                #RESIZE
                im1 = im.resize(MAX_SIZE)
                #save resized images in folder
                im1.save(path)
                print("-> Compressed and saved:", path)
            except:
                print("Compression Error!")
    print("That took {} seconds".format(time.time() - starttime))
    print("Number of failed downloads:",len(failure_ids))

In [ ]:
print("//////DOWNLOADING\\\\\\")
print("Indices",0,"to",len(data_ACS_S)-1)
download_part_ACS_sing(0,len(data_ACS_S))
failures = pd.DataFrame(failure_ids)
failures.to_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/Raw/failures_ACS_Sing.csv")

In [ ]:
#ACS_Singleton
data_ACS_S = pd.read_csv("ACS_Singleton.csv")
print("---ACS_SINGLETON:---")
print("Dataset contains",len(data_ACS_S),"images")
starttime = time.time()
failure_ids = []
for i in range(0,len(data_ACS_S)):
    error = download_image(data_ACS_S["observation_id"][i],"ACS/WFC","HST Singleton")
    if error == "Error":
        failure_ids.append(raw_ids[j])
    else:
        continue
print('That took {} seconds'.format(time.time() - starttime))
print("Number of failed downloads:",len(failure_ids))

---ACS_SINGLETON:---
Dataset contains 204 images
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=je9u01vcq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=je9u01vcq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=je9u01vcq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=je9u01vdq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=je9u01vdq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=je9u01vdq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=je9u01vgq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=je9u01vgq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-act

http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=je7m09fcq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=je7m09fcq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=jef502gpq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=jef502gpq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=jef502gpq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=jeio04fpq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=jeio04fpq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=jeio04fpq_raw.jpg
http://hst.esac.esa.int/ehst-sl-server/servlet/data-action?RETRIEVAL_TYPE=PRODUCT&ARTIFACT_ID=jee304q3q_

KeyboardInterrupt: 

# Count Images

In [ ]:
#Count images since 01-04-2020
data_ACS_R = pd.read_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/ACS_Apr_2020.csv")
print("---ACS_Composite:---")
print("Dataset contains",len(data_ACS_R),"composite images")
print("It contains",data_ACS_R.sum(axis=0)["members_number"],"raw images")

data_WFC3_UVIS = pd.read_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/WFC3_UVIS_Apr_2020.csv")
print("---WFC3_UVIS_Composite:---")
print("Dataset contains",len(data_WFC3_UVIS),"composite images")
print("It contains",data_WFC3_UVIS.sum(axis=0)["members_number"],"raw images")

data_WFC3_IR = pd.read_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/WFC3_IR_Apr_2020.csv")
print("---WFC3_IR_Composite:---")
print("Dataset contains",len(data_WFC3_IR),"composite images")
print("It contains",data_WFC3_IR.sum(axis=0)["members_number"],"raw images")

---ACS_Composite:---
Dataset contains 1240 composite images
It contains 3502 raw images
---WFC3_UVIS_Composite:---
Dataset contains 2515 composite images
It contains 7615 raw images
---WFC3_IR_Composite:---
Dataset contains 1849 composite images
It contains 7941 raw images


In [ ]:
data_WFC3_IR = pd.read_csv("/content/drive/MyDrive/ESA/Data/Hubble_Images/IR_Apr_2020_spectrum.csv")
print("---WFC3_IR_Composite:---")
print("Dataset contains",len(data_WFC3_IR),"composite images")
print("It contains",data_WFC3_IR.sum(axis=0)["members_number"],"raw images")

---WFC3_IR_Composite:---
Dataset contains 322 composite images
It contains 2540 raw images
